In [1]:
import pyLPM
import pandas as pd
import RBFN
import RBF
import numpy as np

In [2]:
walter = pd.read_csv('data/walker.csv')

In [3]:
walter.drop(columns=['Id','U','T'], inplace=True)

In [4]:
walter.head()

X     Y      V
0  11.0   8.0    0.0
1   8.0  30.0    0.0
2   9.0  48.0  224.4
3   8.0  69.0  434.4
4   9.0  90.0  412.1

In [5]:
walter['Z'] = np.zeros(len(walter))

In [6]:
walter.head()

X     Y      V    Z
0  11.0   8.0    0.0  0.0
1   8.0  30.0    0.0  0.0
2   9.0  48.0  224.4  0.0
3   8.0  69.0  434.4  0.0
4   9.0  90.0  412.1  0.0

In [7]:
exhaust = pd.read_csv('data/walker_fivebyfive_exhaust.csv')

In [8]:
exhaust = exhaust.sort_values(by=['YG+ Gravity Center+','XG+ Gravity Center+'])

In [9]:
exhaust.head()

SN+ Sample Number (READONLY)+  XG+ Gravity Center+  YG+ Gravity Center+  \
0                                1                  8.0                  8.0   
58                              59                 13.0                  8.0   
116                            117                 18.0                  8.0   
174                            175                 23.0                  8.0   
232                            233                 28.0                  8.0   

     copy_stat_mean    iqd     ok  ok_pt  
0              7.65   3.41  38.67  38.69  
58             9.37   1.76  28.49  28.45  
116           13.77  20.53  44.10  44.19  
174           51.79  36.18  36.43  36.53  
232           72.53  38.44  33.22  33.15

In [10]:
coordinates = walter[['X','Y','Z']]

In [11]:
RBFN.cluster_centers_evaluation(coordinates=coordinates, 
                                max_num_clusters=40)

# Settinng parameters

In [30]:
n_clus = 200

In [31]:
centers = RBFN.cluster_centers(n_clus=n_clus,
                               coordinates=coordinates)

In [32]:
rbf_n = RBFN.RBFN(cluster_centers=centers, 
          sigma=None)

In [33]:
#rbf_n.knn_sigma_definition(neighbors_number=150)

In [34]:
#rbf_n.sigma

In [35]:
rbf_n.random_bias()

Random bias: 0.48293338740696745


In [36]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [37]:
grid = pyLPM.utils.autogrid(x=walter.X, y=walter.Y, z=walter.Z, sx=5, sy=5, sz=1)

In [38]:
grid

{'ox': 8.0,
 'oy': 8.0,
 'oz': 0.0,
 'sx': 5,
 'sy': 5,
 'sz': 1,
 'nx': 50,
 'ny': 58,
 'nz': 1}

In [39]:
X = pyLPM.utils.add_coord(grid)

In [40]:
predict = rbf_n.predict(X)

In [41]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [42]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=exhaust.copy_stat_mean,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake exhaustive',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [43]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=exhaust.iqd,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake IQD',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [44]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=exhaust.ok_pt,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake ordinary kriging',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [45]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

In [46]:
pyLPM.plots.scatter2d(x=exhaust.ok_pt, y=exhaust.copy_stat_mean)

In [47]:
pyLPM.plots.scatter2d(x=exhaust.iqd, y=exhaust.copy_stat_mean)

# Traditional RBF

In [112]:
traditional_rbf = RBF.RBF(0.222,1,1,0,0,0, function='gaussian')

In [113]:
traditional_rbf.fit(coordinates.values, walter.V.values)

In [114]:
traditional_predictions = traditional_rbf.predict(X)

In [115]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=traditional_predictions,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [116]:
pyLPM.plots.scatter2d(x=traditional_predictions, y=exhaust.copy_stat_mean)

# tradidional anisotropic

In [117]:
traditional_anis_rbf = RBF.RBF(1.7,2,1,160,0,0, function='multiquadratic')

In [118]:
traditional_anis_rbf.fit(coordinates.values, walter.V.values)

In [119]:
traditional_anis_predictions = traditional_anis_rbf.predict(X)

In [120]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=traditional_anis_predictions,
    categorical=False,
    #points=[walter.X, walter.Y, walter.V],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [121]:
pyLPM.plots.scatter2d(x=traditional_anis_predictions, y=exhaust.copy_stat_mean)

# python RBF

In [ ]:
from scipy.interpolate import Rbf

In [ ]:
rbfi = Rbf(coordinates.X, coordinates.Y, coordinates.Z, walter.V, epsilon=1.7)

In [ ]:
predict_python = rbfi(X.T[0], X.T[1], X.T[2])

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_python,
    categorical=False,
    #points=[walter.X, walter.Y, walter.V],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_python, y=exhaust.copy_stat_mean)

## Anisotropic

In [ ]:
rbf_anis = RBFN.RBFN(cluster_centers=centers, sigma=None, major_med=1.4, major_min=1, azimuth=160,dip=0,rake=0)

In [ ]:
#rbf_anis.knn_sigma_definition(neighbors_number=120)

In [ ]:
rbf_anis.fit(X=coordinates.values, 
          y=walter.V.values)

In [ ]:
predict = rbf_anis.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

# Train

In [ ]:
X_train, X_test, y_train, y_test = RBFN.train_test_sets_builder(walter, 'X', 'Y', 'Z', 'V')

In [ ]:
rbf_n.train(8000, X_train, X_test, y_train, y_test, learning_rate_w=0.001)

In [ ]:
predict_train = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_train,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_train, y=exhaust.copy_stat_mean)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
predict_random_weights = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_random_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_random_weights, y=exhaust.copy_stat_mean, xy_line=False, best_fit_line=False)

In [ ]:
rbf_n.train(2000, X_train, X_test, y_train, y_test, learning_rate_w=0.0008)

In [ ]:
predict_trained_weights = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_weights,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_weights, y=exhaust.copy_stat_mean)

# Trainign with NN

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=3, learning_rate_w=0.0006)

In [ ]:
predict_trained_knn = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn, y=exhaust.copy_stat_mean)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.train(3000, X_train, X_test, y_train, y_test, neighbors_number=6, learning_rate_w=0.0006)

In [ ]:
predict_trained_knn_6 = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_6,
    categorical=False,
    points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn_6, y=predict_trained_knn)

In [ ]:
rbf_n.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n.fit(X=coordinates.values, 
          y=walter.V.values)

In [ ]:
rbf_n.train(6000, X_train, X_test, y_train, y_test, neighbors_number=5, learning_rate_w=0.003)

In [ ]:
predict_trained_knn_from_fit = rbf_n.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_trained_knn_from_fit,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_trained_knn_from_fit, y=exhaust.copy_stat_mean)

## anis train

In [ ]:
rbf_anis.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_anis.train(6000, X_train, X_test, y_train, y_test, neighbors_number=None, learning_rate_w=0.0003)

In [ ]:
predict_anist = rbf_anis.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict_anist,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict_anist, y=exhaust.copy_stat_mean)

# Multiquadratic

In [122]:
rbf_n_mq = RBFN.RBFN(cluster_centers=centers, 
          sigma=None,
          function='multiquadratic')

In [123]:
#rbf_n_mq.knn_sigma_definition(1)

In [129]:
#rbf_n_mq.sigma

In [125]:
rbf_n_mq.fit(X=coordinates.values, 
             y=walter.V.values)

In [126]:
predict = rbf_n_mq.predict(X)

In [127]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [128]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

# multiquadratic anis

In [ ]:
rbf_n_mq_aniso = RBFN.RBFN(cluster_centers=centers, 
          sigma=None,
          function='multiquadratic',
          major_med=1.8,
          major_min=1,
          azimuth=160.0,
          dip=0.0,
          rake=0.0,
)

In [ ]:
rbf_n_mq_aniso.knn_sigma_definition(6)

In [ ]:
rbf_n_mq_aniso.fit(X=coordinates.values, 
             y=walter.V.values)

In [ ]:
predict = rbf_n_mq_aniso.predict(X)

In [ ]:
pyLPM.plots.pixelplot(
    grid_dic=grid,
    variable=predict,
    categorical=False,
    #points=[[x[0] for x in centers[:,0:1]], [y[0] for y in centers[:,1:2]], np.zeros(len(centers))],
    gap=0,
    title='Walker lake RBFN interpolation',
    x_axis='Easting (m)',
    y_axis='Northing (m)',
    colorscale='Jet',
    colorbartitle='',
    figsize=(700, 700),)

In [ ]:
pyLPM.plots.scatter2d(x=predict, y=exhaust.copy_stat_mean)

# train

In [ ]:
rbf_n_mq_aniso.weights = np.random.randn(n_clus+1)

In [ ]:
rbf_n_mq_aniso.train(30, X_train, X_test, y_train, y_test, neighbors_number=None, learning_rate_w=0.007)